In [4]:
import numpy as np
import pandas as pd

df = pd.read_csv(r"C:\Users\deepc\Downloads\orientation-all-data.tsv",sep='\t')
print(df)

        Unnamed: 0       id                           speaker sex  \
0                0  at00000  e1b7e1ca73306cd46456f47a49217674   M   
1                1  at00001  a0e009a76087c85dab31ab2f4575cbed   M   
2                2  at00002  c5b34f33170a3e9ed1e47561128aaea8   M   
3                3  at00003  17af36ebfb1c5a2c0ebacf8a36e39371   M   
4                4  at00004  bb823f32cafcfdcd105f94ce99de3da2   M   
...            ...      ...                               ...  ..   
148938        2540  ua02540  b12f99688d91258769fac1b708a020c0   M   
148939        2541  ua02541  b12f99688d91258769fac1b708a020c0   M   
148940        2542  ua02542  b12f99688d91258769fac1b708a020c0   M   
148941        2543  ua02543  b12f99688d91258769fac1b708a020c0   M   
148942        2544  ua02544  d0154f948e3cb661aaa40e34022f0b7c   F   

                                                     text  \
0       Herr Präsident! Hohes Haus! "Wenn eine Idee mi...   
1       Sehr geehrter Herr Präsident! Hohes Haus!

In [13]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained('bert-base-uncased')

In [11]:
def process_data(row):

    text = row['text_en']
    text = str(text)
    text = ' '.join(text.split())

    encodings = tokenizer(text, padding="max_length", truncation=True, max_length=128)

    label = 0
    if row['label'] == 1:
        label += 1

    encodings['label'] = label
    encodings['text'] = text

    return encodings

In [14]:
processed_data = []

for i in range(len(df)):
    processed_data.append(process_data(df.iloc[i]))

In [15]:
from sklearn.model_selection import train_test_split

new_df = pd.DataFrame(processed_data)

train_df, valid_df = train_test_split(
    new_df,
    test_size=0.2,
    random_state=2022
)

In [16]:
import pyarrow as pa
from datasets import Dataset

train_hg = Dataset(pa.Table.from_pandas(train_df))
valid_hg = Dataset(pa.Table.from_pandas(valid_df))

In [17]:
from transformers import AutoModelForSequenceClassification

model = AutoModelForSequenceClassification.from_pretrained(
    'bert-base-uncased',
    num_labels=2
)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [18]:
from transformers import TrainingArguments, Trainer

training_args = TrainingArguments(output_dir="./result", evaluation_strategy="epoch")

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_hg,
    eval_dataset=valid_hg,
    tokenizer=tokenizer
)

c:\Users\deepc\anaconda3\envs\New_envi1\Lib\site-packages\accelerate\accelerator.py:446: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False)
  warnings.warn(


In [9]:
trainer.train()

  1%|          | 500/44685 [01:10<1:40:29,  7.33it/s]

{'loss': 0.6858, 'learning_rate': 4.944052814143449e-05, 'epoch': 0.03}


  2%|▏         | 1000/44685 [02:22<1:39:07,  7.35it/s]

{'loss': 0.6785, 'learning_rate': 4.888105628286898e-05, 'epoch': 0.07}


  3%|▎         | 1500/44685 [03:32<1:36:07,  7.49it/s]

...

100%|█████████▉| 44500/44685 [1:48:06<00:25,  7.35it/s]

{'loss': 0.6628, 'learning_rate': 2.0700458766924023e-07, 'epoch': 2.99}


                                                       
100%|██████████| 44685/44685 [1:50:53<00:00,  6.72it/s]

{'eval_loss': 0.6688590049743652, 'eval_runtime': 140.3288, 'eval_samples_per_second': 212.28, 'eval_steps_per_second': 26.538, 'epoch': 3.0}
{'train_runtime': 6653.77, 'train_samples_per_second': 53.723, 'train_steps_per_second': 6.716, 'train_loss': 0.6708716389209055, 'epoch': 3.0}


TrainOutput(global_step=44685, training_loss=0.6708716389209055, metrics={'train_runtime': 6653.77, 'train_samples_per_second': 53.723, 'train_steps_per_second': 6.716, 'train_loss': 0.6708716389209055, 'epoch': 3.0})

In [10]:
trainer.evaluate()

100%|██████████| 3724/3724 [02:18<00:00, 26.89it/s]


{'eval_loss': 0.6688590049743652,
 'eval_runtime': 138.5063,
 'eval_samples_per_second': 215.073,
 'eval_steps_per_second': 26.887,
 'epoch': 3.0}

In [12]:
model.save_pretrained('D:/ImageClef/model_final/')

In [1]:
import torch
from transformers import AutoModelForSequenceClassification

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

new_model = AutoModelForSequenceClassification.from_pretrained('D:/ImageClef/model_final/').to(device)
from transformers import AutoTokenizer

new_tokenizer = AutoTokenizer.from_pretrained('bert-base-uncased')

c:\Users\deepc\anaconda3\envs\New_envi1\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
c:\Users\deepc\anaconda3\envs\New_envi1\Lib\site-packages\huggingface_hub-0.23.0-py3.8.egg\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.


In [2]:
import numpy as np

def get_prediction(text):
    encoding = new_tokenizer(text, return_tensors="pt", padding="max_length", truncation=True, max_length=128)
    encoding = {k: v.to(trainer.model.device) for k,v in encoding.items()}

    outputs = new_model(**encoding)

    logits = outputs.logits
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    sigmoid = torch.nn.Sigmoid()
    print(sigmoid)
    probs = sigmoid(logits.squeeze().cpu())
    probs = probs.detach().numpy()
    label = np.argmax(probs, axis=-1)
    
    if label == 1:
        return {
            'Orientation': 'Right',
            'probability': probs[1]
        }
    else:
        return {
            'Orientation': 'Left',
            'probability': probs[0]
        }

In [19]:
correct_l = 0
correct_r = 0
for i in range(len(df)):
    d = get_prediction(str(df['text_en'].iloc[i]))
    print(d)
    if(df['label'].iloc[i]==0 and d['Orientation'] == 'Left'):
        correct_l+=1
    elif(df['label'].iloc[i]==1 and d['Orientation']=='Right'):
        correct_r+=1

print(correct_l,'/',len(df))
print(correct_r,'/',len(df))

Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}
Sigmoid(

KeyboardInterrupt: 

In [20]:
d = get_prediction('Mr President, I would like to Well, I guess Tina Ghasemis gonna have to listen. It was that she wrote the lines herself that was the problem. Thats what I said. The problem was that she wrote them before the debate and therefore could not take the Minister for Employments response into the further debate. Then the debate became a little limp. That she writes them herself, Im absolutely convinced. The problem is that she writes them before the debate, and then the debate becomes a little strange to listen to. <p> I didnt say it was a speech writer who had written her post. I said that it is a danger to base your argumentation on ill-founded so-called stop lines from less talented speech writers at the Moderate Party Office. Thats exactly how I put it. <p> So to the point. We have reviewed the fact that social security contributions for young people have not worked. The job guarantee for young people once carried out by Tina Ghasemis moderate government, what did it lead to? It can be a little interesting to have as a perspective. The only thing it led to was the exclusion of young people from what research says is the most important thing: early intervention. A big stick was put into the machinery and destroyed the ability of many young people to break unemployment by shutting them out of action. That is what the bourgeois guarantee really stood for.')
print(d)

Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}


In [21]:
d = get_prediction('dear andreas wabl! i want to address you right now by saying: we will give our support to that request and to that proposal, which has a chance of a majority in this house. this is really the essential point. we can talk about everything, but: the essence of a coalition is that compromises are found. <p> i also do not think that it is fair to have more than 800 s in attendance than civilian servants. furthermore, i do not think that civil servants are required so much less that it would be justified for them to have served for three and a half months. however, i believe that it is completely incomprehensible, in particular, to maintain or reintroduce a conscience test, a conscience test which was, in fact, the most humane form of the civil service regime of earlier days. <p> it is worth standing up to this compromise that has been agreed here. . i know that in the ranks of the socialist group there are many who would have wanted more and who will continue to work politically in the future to improve the situation of civil servants. <p> i stand here as a former civil servant, so i know what im talking about. ive done this service. anyone who goes out here and claims that this would have been an easy service has no idea what hes talking about, ladies and gentlemen! <p> what is really annoyed by mr wabl â he should say quite openly â is that he knows exactly that the civil servants in minister have a sincere and hard-working representative. the minister will continue to work for them in the future, even if this costs the green votes. <p> i would like to say to mr jung: if he is to submit an application which leads to a reduction in the presence service, for example in the form of holiday entitlements, and we can also reduce the service time for civil servants to the same extent, then i should be right to do so. hell find a contact person in me.')
print(d)

Sigmoid()
{'Orientation': 'Right', 'probability': 0.57432216}


In [ ]:
dear andreas wabl! i want to address you right now by saying: we will give our support to that request and to that proposal, which has a chance of a majority in this house. this is really the essential point. we can talk about everything, but: the essence of a coalition is that compromises are found. <p> i also do not think that it is fair to have more than 800 s in attendance than civilian servants. furthermore, i do not think that civil servants are required so much less that it would be justified for them to have served for three and a half months. however, i believe that it is completely incomprehensible, in particular, to maintain or reintroduce a conscience test, a conscience test which was, in fact, the most humane form of the civil service regime of earlier days. <p> it is worth standing up to this compromise that has been agreed here. . i know that in the ranks of the socialist group there are many who would have wanted more and who will continue to work politically in the future to improve the situation of civil servants. <p> i stand here as a former civil servant, so i know what i'm talking about. i've done this service. anyone who goes out here and claims that this would have been an easy service has no idea what he's talking about, ladies and gentlemen! <p> what is really annoyed by mr wabl â he should say quite openly â is that he knows exactly that the civil servants in minister have a sincere and hard-working representative. the minister will continue to work for them in the future, even if this costs the green votes. <p> i would like to say to mr jung: if he is to submit an application which leads to a reduction in the presence service, for example in the form of holiday entitlements, and we can also reduce the service time for civil servants to the same extent, then i should be right to do so. he'll find a contact person in me.